In [1]:
import sys
import numpy as np
import sklearn
import rdkit
import xgboost
import matplotlib

# Check Python version
print(f"Python Version: {sys.version}")

# Check package versions
print(f"NumPy Version: {np.__version__}")
print(f"Scikit-learn Version: {sklearn.__version__}")
print(f"RDKit Version: {rdkit.__version__}")
print(f"XGBoost Version: {xgboost.__version__}")
print(f"Matplotlib Version: {matplotlib.__version__}")

Python Version: 3.10.16 | packaged by Anaconda, Inc. | (main, Dec 11 2024, 16:19:12) [MSC v.1929 64 bit (AMD64)]
NumPy Version: 1.26.4
Scikit-learn Version: 1.6.1
RDKit Version: 2024.09.1
XGBoost Version: 2.1.3
Matplotlib Version: 3.10.0


In [2]:
import pandas as pd
import numpy as np
from rdkit import Chem, RDLogger
from rdkit.Chem import Descriptors, AllChem, RemoveHs
from sklearn.preprocessing import StandardScaler
from tqdm import tqdm
import warnings
from joblib import load, dump

# Ignore specific deprecation warnings
warnings.filterwarnings("ignore", category=DeprecationWarning, message=".*Morgan.*")

In [3]:
# Load the filtered training dataset
train_data = pd.read_csv(r'E:\OneDrive - UCLA IT Services\UCLA\PhD Project\CoMPAIT\Filtered_Train.csv')
pred_data = pd.read_csv(r'E:\OneDrive - UCLA IT Services\UCLA\PhD Project\CoMPAIT\PredictionSet.csv')

# Extract SMILES strings and target values
SMILES_train = train_data['QSAR_READY_SMILES']
SMILES_prediction = pred_data['QSAR_ready_SMILES']
Endpoint1 = train_data['4_hr_value_mgL']
Endpoint2 = train_data['4_hr_value_ppm']

#Train part
# 1. Generate RDKit descriptor features
mol_list = [Chem.MolFromSmiles(smiles) for smiles in SMILES_train]
descriptor_names = [desc_name[0] for desc_name in Descriptors._descList]

descriptors = []
for mol in tqdm(mol_list, desc="Calculating RDKit descriptors"):
    if mol is not None:
        descriptor_values = []
        for desc_name, desc_fn in Descriptors._descList:
            try:
                descriptor_values.append(desc_fn(mol))
            except Exception as e:
                descriptor_values.append(np.nan)
        descriptors.append(descriptor_values)
    else:
        descriptors.append([np.nan] * len(descriptor_names))

# Convert descriptors to DataFrame
descriptor_df = pd.DataFrame(descriptors, columns=descriptor_names)

# Check for NaN values in descriptors
print(f"NaN values in descriptor DataFrame before cleaning: {descriptor_df.isna().sum().sum()}")

# Remove columns with infinity or values greater than 1e5
descriptor_df = descriptor_df.loc[:, ~(descriptor_df.replace([np.inf, -np.inf], 1e10).abs() > 1e5).any()]

# Standardize descriptor features
scaler = StandardScaler()
X_des = scaler.fit_transform(descriptor_df.values)

# Save the scaler for later use in predictions
dump(scaler, 'scaler.pkl')
print(f"Descriptor feature shape: {X_des.shape}")

# Save the final descriptor columns for later use
train_descriptor_columns = descriptor_df.columns
print(f"Saving {len(train_descriptor_columns)} columns to train_descriptor_columns.pkl")
dump(train_descriptor_columns, 'train_descriptor_columns.pkl')

# 2. Generate fingerprint features
def morgan_fingerprints(smiles_list):
    fingerprints = []
    for sm in tqdm(smiles_list, desc="Generating Morgan fingerprints"):
        mol = Chem.MolFromSmiles(sm)
        if mol is not None:
            try:
                fpts = AllChem.GetMorganFingerprintAsBitVect(mol, radius=2, nBits=1024)
                fingerprints.append(np.array(fpts))
            except Exception as e:
                print(f"Error generating fingerprint for molecule: {sm}, Error: {e}")
                fingerprints.append(np.array([np.nan] * 1024))
        else:
            print(f"Invalid SMILES: {sm}")
            fingerprints.append(np.array([np.nan] * 1024))
    return np.array(fingerprints)

Morgan_fpts = morgan_fingerprints(SMILES_train)

# Convert Morgan fingerprints to DataFrame
X_fp = pd.DataFrame(Morgan_fpts, columns=[f'Bit_{i}' for i in range(1024)])

# Check for NaN values in fingerprints
nan_count_fp = np.isnan(X_fp).sum()
print(f'Total NaN values in Morgan fingerprints: {nan_count_fp}')
print(f"Descriptor feature shape: {X_fp.shape}")

# Combine reduced RDKit descriptors and fingerprints
X_combined = np.hstack([X_des, X_fp.values])
print(f"Final combined feature shape: {X_combined.shape}")

Calculating RDKit descriptors: 100%|██████████| 594/594 [00:01<00:00, 341.71it/s]


NaN values in descriptor DataFrame before cleaning: 0
Descriptor feature shape: (594, 209)
Saving 209 columns to train_descriptor_columns.pkl


Generating Morgan fingerprints:   0%|          | 0/594 [00:00<?, ?it/s][17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use MorganGenerator
[17:40:39] DEPRECATION WARNING: please use M

Total NaN values in Morgan fingerprints: Bit_0       0
Bit_1       0
Bit_2       0
Bit_3       0
Bit_4       0
           ..
Bit_1019    0
Bit_1020    0
Bit_1021    0
Bit_1022    0
Bit_1023    0
Length: 1024, dtype: int64
Descriptor feature shape: (594, 1024)
Final combined feature shape: (594, 1233)


In [5]:
from sklearn.model_selection import KFold
from sklearn.metrics import mean_squared_error, r2_score
import xgboost as xgb
from sklearn.utils import shuffle

# Cross-validation with 10 splits
kf = KFold(n_splits=10, shuffle=True, random_state=42)

# Function to perform cross-validation, evaluate metrics, and save the best model
def cross_validate_model(X, y):
    n_samples = len(y)
    predictions_all = np.zeros(n_samples)
    rmse_all = []
    r2_all = []

    global_best_model = None
    global_best_rmse = float('inf')
    
    # Cross-validation loop
    for i, (train_index, test_index) in enumerate(kf.split(X, y)):
        print(f'Split: {i + 1} (dataset)')
        train_index_shuffle = shuffle(train_index, random_state=42)
        sub_train_index = train_index_shuffle[:int(len(train_index) * 0.8)]
        sub_valid_index = train_index_shuffle[int(len(train_index) * 0.8):]

        train_feature, train_label = X[sub_train_index], y[sub_train_index]
        valid_feature, valid_label = X[sub_valid_index], y[sub_valid_index]
        test_feature, test_label = X[test_index], y[test_index]

        # Hyperparameters to tune
        learning_rates = [0.01, 0.05, 0.1, 0.2]
        max_depths = [2, 4, 8, 16]
        n_estimators = [100, 200, 400, 800, 1600]

        best_valid_rmse = float('inf')
        best_model_local = None
        best_lr = None
        best_md = None
        best_ne = None

        for lr in learning_rates:
            for md in max_depths:
                for ne in n_estimators:
                    model = xgb.XGBRegressor(learning_rate=lr, max_depth=md, n_estimators=ne, objective='reg:squarederror', random_state=42)
                    model.fit(train_feature, train_label, eval_set=[(valid_feature, valid_label)], verbose=False)
                    valid_preds = model.predict(valid_feature)
                    valid_rmse = np.sqrt(mean_squared_error(valid_label, valid_preds))

                    if valid_rmse < best_valid_rmse:
                        best_valid_rmse = valid_rmse
                        best_model_local = model
                        best_lr = lr
                        best_md = md
                        best_ne = ne

        print(f'Best learning_rate: {best_lr}, Best max_depth: {best_md}, Best n_estimators: {best_ne}')

        # Use the best model to predict the test set
        test_preds = best_model_local.predict(test_feature)
        test_rmse = np.sqrt(mean_squared_error(test_label, test_preds))
        test_r2 = r2_score(test_label, test_preds)

        predictions_all[test_index] = test_preds

        rmse_all.append(test_rmse)
        r2_all.append(test_r2)

        # Track the global best model
        if best_valid_rmse < global_best_rmse:
            global_best_rmse = best_valid_rmse
            global_best_model = best_model_local
            
    # Calculate overall metrics based on combined predictions
    overall_rmse = np.sqrt(mean_squared_error(y, predictions_all))
    overall_r2 = r2_score(y, predictions_all)

    print(f'Test RMSE for Each Fold: {rmse_all}')
    print(f'Mean Test RMSE: {np.mean(rmse_all):.4f}')
    print(f'Overall RMSE: {overall_rmse:.4f}')
    print(f'Overall R2: {overall_r2:.4f}')

    # Create a summary dataframe for easy logging
    summary_df = pd.DataFrame({
        'Fold': range(1, len(rmse_all) + 1),
        'RMSE': rmse_all,
        'R2': r2_all
    })
    print(f'Cross-validation Summary:\n{summary_df}')
    
    # Save the global best model
    global_best_model.save_model(r'E:\OneDrive - UCLA IT Services\UCLA\PhD Project\CoMPAIT\xgb_best_model.json')

cross_validate_model(X_combined, Endpoint2)

Split: 1 (dataset)
Best learning_rate: 0.2, Best max_depth: 4, Best n_estimators: 800
Split: 2 (dataset)
Best learning_rate: 0.05, Best max_depth: 4, Best n_estimators: 1600
Split: 3 (dataset)
Best learning_rate: 0.2, Best max_depth: 4, Best n_estimators: 200
Split: 4 (dataset)
Best learning_rate: 0.05, Best max_depth: 4, Best n_estimators: 100
Split: 5 (dataset)
Best learning_rate: 0.2, Best max_depth: 4, Best n_estimators: 800
Split: 6 (dataset)
Best learning_rate: 0.1, Best max_depth: 4, Best n_estimators: 100
Split: 7 (dataset)
Best learning_rate: 0.1, Best max_depth: 4, Best n_estimators: 200
Split: 8 (dataset)
Best learning_rate: 0.1, Best max_depth: 8, Best n_estimators: 800
Split: 9 (dataset)
Best learning_rate: 0.01, Best max_depth: 8, Best n_estimators: 400
Split: 10 (dataset)
Best learning_rate: 0.05, Best max_depth: 2, Best n_estimators: 400
Test RMSE for Each Fold: [1.13198024609532, 1.080578645864907, 1.022017232701233, 0.8731245195224403, 1.0623626965816992, 0.7537413351

In [6]:
#Prediction part
# Filter SMILES that cannot be converted to fingerprints
filtered_SMILES_fp = []
invalid_SMILES_fp = []

for sm in SMILES_prediction:
    mol = Chem.MolFromSmiles(sm)
    if mol is not None:
        try:
            _ = AllChem.GetMorganFingerprintAsBitVect(mol, radius=2, nBits=1024)
            filtered_SMILES_fp.append(sm)
        except Exception as e:
            invalid_SMILES_fp.append(sm)
    else:
        invalid_SMILES_fp.append(sm)

print(f"Total SMILES invalid for fingerprints: {len(invalid_SMILES_fp)}")

# Verify remaining SMILES can be converted by RDKit
filtered_SMILES_pred = []
invalid_SMILES_rdkit = []

for sm in filtered_SMILES_fp:
    mol = Chem.MolFromSmiles(sm)
    if mol is not None:
        filtered_SMILES_pred.append(sm)
    else:
        invalid_SMILES_rdkit.append(sm)

print(f"Total SMILES invalid for RDKit: {len(invalid_SMILES_rdkit)}")
SMILES_prediction_filtered = filtered_SMILES_pred

# Create a new filtered prediction dataset
filtered_prediction_data = pred_data[pred_data['QSAR_ready_SMILES'].isin(SMILES_prediction_filtered)]

# Generate RDKit descriptor features for prediction data
mol_list_pred = [Chem.MolFromSmiles(sm) for sm in SMILES_prediction_filtered]
descriptor_names = [desc_name[0] for desc_name in Descriptors._descList]

descriptors_pred = []
for mol in tqdm(mol_list_pred, desc="Calculating RDKit descriptors for prediction data"):
    if mol is not None:
        descriptor_values = []
        for desc_name, desc_fn in Descriptors._descList:
            try:
                descriptor_values.append(desc_fn(mol))
            except Exception as e:
                descriptor_values.append(np.nan)
        descriptors_pred.append(descriptor_values)
    else:
        descriptors_pred.append([np.nan] * len(descriptor_names))

# Convert descriptors to DataFrame
descriptor_pred_df = pd.DataFrame(descriptors_pred, columns=descriptor_names)

# Replace inf and -inf with NaN explicitly
num_inf_replaced = descriptor_pred_df.isin([np.inf, -np.inf]).sum().sum()
descriptor_pred_df.replace([np.inf, -np.inf], np.nan, inplace=True)
print(f"Replaced {num_inf_replaced} cells with inf or -inf to NaN.")

# Replace extremely large values (>1e5) with NaN
num_large_values_replaced = (descriptor_pred_df.abs() > 1e5).sum().sum()
descriptor_pred_df[(descriptor_pred_df.abs() > 1e5)] = np.nan
print(f"Replaced {num_large_values_replaced} cells with values >1e5 to NaN.")

# Fill NaN values with 0
num_nan_replaced = descriptor_pred_df.isna().sum().sum()
descriptor_pred_df.fillna(0, inplace=True)
print(f"Replaced {num_nan_replaced} NaN cells with 0.")

[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerator
[18:18:18] DEPRECATION WARNING: please use MorganGenerat

Total SMILES invalid for fingerprints: 55
Total SMILES invalid for RDKit: 0


Calculating RDKit descriptors for prediction data: 100%|██████████| 47714/47714 [03:51<00:00, 205.95it/s]


Replaced 4 cells with inf or -inf to NaN.
Replaced 13028 cells with values >1e5 to NaN.
Replaced 14396 NaN cells with 0.


In [7]:
# Drop columns not in training feature list
train_descriptor_columns = load('train_descriptor_columns.pkl')  # Load saved column names from training
descriptor_pred_df = descriptor_pred_df[descriptor_pred_df.columns.intersection(train_descriptor_columns)]
print(f"there are {descriptor_pred_df.shape} feature in pred dataset feature")

there are (47714, 209) feature in pred dataset feature


In [8]:
# Load the scaler saved during training
scaler = load('scaler.pkl')
X_des_pred = scaler.transform(descriptor_pred_df.values)

# Generate Morgan fingerprints for prediction data
Morgan_fpts_pred = []
for sm in tqdm(SMILES_prediction_filtered, desc="Generating Morgan fingerprints"):
    mol = Chem.MolFromSmiles(sm)
    if mol is not None:
        try:
            fpts = AllChem.GetMorganFingerprintAsBitVect(mol, radius=2, nBits=1024)
            Morgan_fpts_pred.append(np.array(fpts))
        except Exception as e:
            Morgan_fpts_pred.append(np.array([np.nan] * 1024))
    else:
        Morgan_fpts_pred.append(np.array([np.nan] * 1024))

# Convert fingerprints to DataFrame
X_fp_pred = pd.DataFrame(Morgan_fpts_pred, columns=[f'Bit_{i}' for i in range(1024)])

# Replace NaN values in fingerprints
X_fp_pred.fillna(0, inplace=True)

# Combine descriptors and fingerprints
X_combined_pred = np.hstack([X_des_pred, X_fp_pred.values])

# Ensure prediction features match training features
X_combined_train_features = X_combined  # Training features
X_combined_pred_features = X_combined_pred[:, :X_combined_train_features.shape[1]]

print(f"Final combined prediction feature shape: {X_combined_pred_features.shape}")

# Load the best model
best_model = xgb.Booster()
best_model.load_model(r'E:\OneDrive - UCLA IT Services\UCLA\PhD Project\CoMPAIT\xgb_best_model.json')

# Make predictions
pred_dmatrix = xgb.DMatrix(X_combined_pred_features)
predictions_ppm = best_model.predict(pred_dmatrix)

# Add predictions as a new column to the filtered dataset
filtered_prediction_data['prediction_ppm'] = predictions_ppm

# Save the final dataset to CSV
filtered_prediction_data.to_csv(r'E:\OneDrive - UCLA IT Services\UCLA\PhD Project\CoMPAIT\Prediction_Results.csv', index=False)
print("Predictions saved successfully.")

Generating Morgan fingerprints:   0%|          | 0/47714 [00:00<?, ?it/s][18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use MorganGenerator
[18:22:37] DEPRECATION WARNING: please use

Final combined prediction feature shape: (47714, 1233)
Predictions saved successfully.


C:\Users\17954\AppData\Local\Temp\ipykernel_23584\3428332639.py:42: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_prediction_data['prediction_ppm'] = predictions_ppm
